#### **Objective**

The goal is to benchmark different portfolio selection strategies. The idea is to simulate investing 10,000 USD at the beginning of each month using different portfolio allocation models, and then compare which strategy delivers the best performance over time.

The comparison will be based on:

- The evolution of the portfolio's total value over time.
- The allocation method used each month (e.g., Markowitz, equal-weight, etc.).
- Key metrics such as total return, volatility, and Sharpe ratio.

#### **1. Imports**

In [1]:
# %pip install selenium pandas

In [2]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import random
import yfinance as yf
from datetime import datetime
from dateutil.relativedelta import relativedelta
import numpy as np

#### **2. Variables**

In [3]:
adjusted_close_prices_csv = 'data/adjusted_close_prices.csv'


search_all_tickers_flag = False
adjusted_closes_flag = False

#####################################

# search_all_tickers_flag = True
# adjusted_closes_flag = True

##### **2. Download - Asset Dataset**

In [4]:
MAX_ATTEMPTS = 10
BASE_URL = "https://finviz.com/screener.ashx"

USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64)",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7)",
    "Mozilla/5.0 (X11; Linux x86_64)",
    "Mozilla/5.0 (Windows NT 6.1; Win64; x64)",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 12_4)"
]

def scrape_finviz_by_exchange_requests(exchange: str):
    exchange_map = {
        "nasdaq": "exch_nasd",
        "nyse": "exch_nyse"
    }

    if exchange.lower() not in exchange_map:
        raise ValueError("Invalid exchange. Use 'nasdaq' or 'nyse'.")

    exchange_code = exchange_map[exchange.lower()]
    all_data = []
    r = 1  # page offset

    while True:
        success = False
        attempts = 0

        while not success and attempts < MAX_ATTEMPTS:
            try:
                headers = {
                    "User-Agent": random.choice(USER_AGENTS)
                }
                params = {
                    "v": "111",
                    "f": exchange_code,
                    "r": r
                }
                response = requests.get(BASE_URL, headers=headers, params=params, timeout=10)
                if response.status_code == 429:
                    raise Exception("HTTP 429 Too Many Requests")
                response.raise_for_status()

                soup = BeautifulSoup(response.text, "html.parser")
                tables = soup.find_all("table")

                target_table = None
                for table in tables:
                    rows = table.find_all("tr")
                    if len(rows) < 2:
                        continue
                    cols = rows[1].find_all("td")
                    if len(cols) >= 11 and cols[0].text.strip().isdigit():
                        target_table = table
                        break

                if not target_table:
                    raise ValueError("No valid table found.")

                rows = target_table.find_all("tr")[1:]
                if not rows:
                    print(f"No more data on page starting at {r}. Stopping.")
                    return finalize(all_data, exchange)

                for row in rows:
                    cols = row.find_all("td")
                    if len(cols) >= 11:
                        ticker = cols[1].text.strip()
                        company = cols[2].text.strip()
                        sector = cols[3].text.strip()
                        industry = cols[4].text.strip()
                        country = cols[5].text.strip()
                        market_cap = cols[6].text.strip()
                        volume = cols[10].text.strip()
                        all_data.append([ticker, company, sector, industry, country, market_cap, volume])

                print(f"Page {r} OK")
                success = True
                r += 20

                # Simula navegação humana
                time.sleep(random.uniform(3, 6))

            except Exception as e:
                attempts += 1
                print(f"Error on page {r}, attempt {attempts}: {e}")
                time.sleep(5 * attempts + random.uniform(1, 3))  # backoff crescente

        if not success:
            print(f"\n⚠️  Page {r} failed {MAX_ATTEMPTS} times. Finalizing with partial data.")
            return finalize(all_data, exchange)

def finalize(all_data, exchange):
    df = pd.DataFrame(all_data, columns=[
        "Ticker", "Company", "Sector", "Industry", "Country", "Market Cap", "Volume"
    ])
    df = df[df["Volume"] != "0"].reset_index(drop=True)
    filename = f"data/tickers_{exchange.lower()}.csv"
    df.to_csv(filename, index=False)
    print(f"\n✅ Scraping finished. Saved {len(df)} tickers to '{filename}'")
    return df


##### **2.1 Nasdaq Tickers**

In [5]:
if search_all_tickers_flag:
    nasdaq = scrape_finviz_by_exchange_requests("nasdaq")
    nasdaq

nasdaq = pd.read_csv("data/tickers_nasdaq.csv")
nasdaq

Ticker                                            Company  \
0      AACB                          Artius II Acquisition Inc   
1      AACG                          ATA Creativity Global ADR   
2      AACI                        Armada Acquisition Corp. II   
3      AADR                AdvisorShares Dorsey Wright ADR ETF   
4       AAL                        American Airlines Group Inc   
...     ...                                                ...   
4231   ZVSA                           ZyVersa Therapeutics Inc   
4232   ZYBT                  Zhengye Biotechnology Holding Ltd   
4233   ZYME                                   Zymeworks BC Inc   
4234   ZYXI                                          Zynex Inc   
4235    ZZZ  Cyber Hornet S&P 500 and Bitcoin 75 /25 Strate...   

                  Sector                                  Industry Country  \
0              Financial                           Shell Companies     USA   
1     Consumer Defensive             Education & Training Services   China   
2              Financial                           Shell Companies     USA   
3              Financial                      Exchange Traded Fund     USA   
4            Industrials                                  Airlines     USA   
...                  ...                                       ...     ...   
4231          Healthcare                             Biotechnology     USA   
4232          Healthcare  Drug Manufacturers - Specialty & Generic   China   
4233          Healthcare                             Biotechnology     USA   
4234          Healthcare                      Medical Distribution     USA   
4235           Financial                      Exchange Traded Fund     USA   

     Market Cap      Volume  
0       298.12M           1  
1        67.45M     254,981  
2       321.12M           3  
3             -          20  
4         7.28B  24,043,012  
...         ...         ...  
4231      0.93M      18,248  
4232    256.85M       6,705  
4233    879.92M     402,780  
4234     42.03M     840,704  
4235          -         809  

[4236 rows x 7 columns]

##### **2.2 Nyse Tickers**


In [6]:
if search_all_tickers_flag:
    nyse = scrape_finviz_by_exchange_requests("nyse")
    nyse

nyse = pd.read_csv("data/tickers_nyse.csv")
nyse

Ticker                                         Company  \
0         A                        Agilent Technologies Inc   
1        AA                                      Alcoa Corp   
2       AAA  Alternative Access First Priority CLO Bond ETF   
3      AACT                 Ares Acquisition Corporation II   
4       AAM                     AA Mission Acquisition Corp   
...     ...                                             ...   
4669    ZTO                    ZTO Express (Cayman) Inc ADR   
4670    ZTR                    Virtus Total Return Fund Inc   
4671    ZTS                                      Zoetis Inc   
4672   ZVIA                                       Zevia PBC   
4673    ZWS                 Zurn Elkay Water Solutions Corp   

                  Sector                                  Industry Country  \
0             Healthcare                    Diagnostics & Research     USA   
1        Basic Materials                                  Aluminum     USA   
2              Financial                      Exchange Traded Fund     USA   
3              Financial                           Shell Companies     USA   
4              Financial                           Shell Companies     USA   
...                  ...                                       ...     ...   
4669         Industrials            Integrated Freight & Logistics   China   
4670           Financial                  Closed-End Fund - Equity     USA   
4671          Healthcare  Drug Manufacturers - Specialty & Generic     USA   
4672  Consumer Defensive                 Beverages - Non-Alcoholic     USA   
4673         Industrials            Pollution & Treatment Controls     USA   

     Market Cap     Volume  
0        32.14B    682,198  
1         7.44B  3,594,093  
2             -      6,048  
3       705.51M    209,977  
4       459.97M      2,413  
...         ...        ...  
4669     12.03B  2,439,145  
4670    342.65M    128,272  
4671     65.41B  1,582,264  
4672    219.33M    239,408  
4673      7.41B  1,115,303  

[4674 rows x 7 columns]

In [7]:
tickers = pd.concat([nasdaq, nyse], ignore_index=True)
tickers

Ticker                              Company              Sector  \
0      AACB            Artius II Acquisition Inc           Financial   
1      AACG            ATA Creativity Global ADR  Consumer Defensive   
2      AACI          Armada Acquisition Corp. II           Financial   
3      AADR  AdvisorShares Dorsey Wright ADR ETF           Financial   
4       AAL          American Airlines Group Inc         Industrials   
...     ...                                  ...                 ...   
8905    ZTO         ZTO Express (Cayman) Inc ADR         Industrials   
8906    ZTR         Virtus Total Return Fund Inc           Financial   
8907    ZTS                           Zoetis Inc          Healthcare   
8908   ZVIA                            Zevia PBC  Consumer Defensive   
8909    ZWS      Zurn Elkay Water Solutions Corp         Industrials   

                                      Industry Country Market Cap      Volume  
0                              Shell Companies     USA    298.12M           1  
1                Education & Training Services   China     67.45M     254,981  
2                              Shell Companies     USA    321.12M           3  
3                         Exchange Traded Fund     USA          -          20  
4                                     Airlines     USA      7.28B  24,043,012  
...                                        ...     ...        ...         ...  
8905            Integrated Freight & Logistics   China     12.03B   2,439,145  
8906                  Closed-End Fund - Equity     USA    342.65M     128,272  
8907  Drug Manufacturers - Specialty & Generic     USA     65.41B   1,582,264  
8908                 Beverages - Non-Alcoholic     USA    219.33M     239,408  
8909            Pollution & Treatment Controls     USA      7.41B   1,115,303  

[8910 rows x 7 columns]

#### **3. Process data**


In [8]:
tickers['Volume'] = tickers['Volume'].str.replace(',', '').astype(float)
tickers.sort_values(by="Volume", inplace=True, ascending=False)
tickers

Ticker                                            Company  \
2236   LOBO                           Lobo Ev Technologies Ltd   
3138   RAYA                    Erayak Power Solution Group Inc   
3724   TNON                                  Tenon Medical Inc   
8060   SOXS        Direxion Daily Semiconductor Bear 3X Shares   
2010   IXHL                            Incannex Healthcare Inc   
...     ...                                                ...   
6555   JDVI  John Hancock Disciplined Value International S...   
6656   KBUF  KraneShares 90% KWEB Defined Outcome January 2...   
4490   AUSM                Allspring Ultra Short Municipal ETF   
7753   ROPE                            Coastal Compass 100 ETF   
0      AACB                          Artius II Acquisition Inc   

                 Sector                                  Industry    Country  \
2236  Consumer Cyclical                        Auto Manufacturers      China   
3138        Industrials              Electrical Equipment & Parts      China   
3724         Healthcare                           Medical Devices        USA   
8060          Financial                      Exchange Traded Fund        USA   
2010         Healthcare  Drug Manufacturers - Specialty & Generic  Australia   
...                 ...                                       ...        ...   
6555          Financial                      Exchange Traded Fund        USA   
6656          Financial                      Exchange Traded Fund        USA   
4490          Financial                      Exchange Traded Fund        USA   
7753          Financial                      Exchange Traded Fund        USA   
0             Financial                           Shell Companies        USA   

     Market Cap       Volume  
2236     13.39M  277221913.0  
3138      4.35M  229545591.0  
3724     12.22M  211413022.0  
8060          -  200627421.0  
2010     38.40M  137451462.0  
...         ...          ...  
6555          -          1.0  
6656          -          1.0  
4490          -          1.0  
7753          -          1.0  
0       298.12M          1.0  

[8910 rows x 7 columns]

#### **4. Filter assets**

##### **4.1 Liquidity: Remove low liquidity**
- Filters out assets with insufficient daily trading volume.

In [9]:
tickers = tickers[tickers['Volume'] > 500_000]
tickers

Ticker                                      Company              Sector  \
2236   LOBO                     Lobo Ev Technologies Ltd   Consumer Cyclical   
3138   RAYA              Erayak Power Solution Group Inc         Industrials   
3724   TNON                            Tenon Medical Inc          Healthcare   
8060   SOXS  Direxion Daily Semiconductor Bear 3X Shares           Financial   
2010   IXHL                      Incannex Healthcare Inc          Healthcare   
...     ...                                          ...                 ...   
3060   QDEL                      QuidelOrtho Corporation          Healthcare   
7009    MPC                      Marathon Petroleum Corp              Energy   
8065   SPBO            SPDR Portfolio Corporate Bond ETF           Financial   
4586     BC                               Brunswick Corp   Consumer Cyclical   
3107    QSG                     QuantaSing Group Ltd ADR  Consumer Defensive   

                                      Industry    Country Market Cap  \
2236                        Auto Manufacturers      China     13.39M   
3138              Electrical Equipment & Parts      China      4.35M   
3724                           Medical Devices        USA     12.22M   
8060                      Exchange Traded Fund        USA          -   
2010  Drug Manufacturers - Specialty & Generic  Australia     38.40M   
...                                        ...        ...        ...   
3060                           Medical Devices        USA      1.53B   
7009            Oil & Gas Refining & Marketing        USA     50.94B   
8065                      Exchange Traded Fund        USA          -   
4586                     Recreational Vehicles        USA      3.70B   
3107             Education & Training Services      China    285.02M   

           Volume  
2236  277221913.0  
3138  229545591.0  
3724  211413022.0  
8060  200627421.0  
2010  137451462.0  
...           ...  
3060     502153.0  
7009     500904.0  
8065     500751.0  
4586     500656.0  
3107     500305.0  

[2034 rows x 7 columns]

##### **4.2 Market Cap: Remove small or undefined market capitalization**
- Excludes microcaps and assets without valid market capitalization data to reduce exposure to volatility, manipulation, and poor fundamentals.

In [10]:
# Remove null or invalid Market Cap values
tickers = tickers[tickers['Market Cap'] != '-'].copy()

# Convert Market Cap to numeric format
def convert_market_cap(val):
    val = val.replace('$', '').replace(',', '').strip()
    if val.endswith('B'):
        return float(val.replace('B', '')) * 1e9
    elif val.endswith('M'):
        return float(val.replace('M', '')) * 1e6
    elif val.endswith('K'):
        return float(val.replace('K', '')) * 1e3
    else:
        return float(val)

tickers['market_cap'] = tickers['Market Cap'].apply(convert_market_cap)

# Filter by Volume and Market Cap
tickers = tickers[
    (tickers['market_cap'] > 500_000_000)
]
tickers

Ticker                    Company             Sector  \
2754   OPEN  Opendoor Technologies Inc        Real Estate   
2649   NVDA                NVIDIA Corp         Technology   
212    AMZN             Amazon.com Inc  Consumer Cyclical   
7153    NIO                NIO Inc ADR  Consumer Cyclical   
8547   VALE              Vale S.A. ADR    Basic Materials   
...     ...                        ...                ...   
6706   KODK           Eastman Kodak Co        Industrials   
4359   ALLE               Allegion plc        Industrials   
3060   QDEL    QuidelOrtho Corporation         Healthcare   
7009    MPC    Marathon Petroleum Corp             Energy   
4586     BC             Brunswick Corp  Consumer Cyclical   

                              Industry  Country Market Cap       Volume  \
2754              Real Estate Services      USA      1.49B  126981253.0   
2649                    Semiconductors      USA   4306.36B  106136868.0   
212                    Internet Retail      USA   2294.14B   57251389.0   
7153                Auto Manufacturers    China      9.45B   56365932.0   
8547  Other Industrial Metals & Mining   Brazil     41.58B   55509604.0   
...                                ...      ...        ...          ...   
6706       Specialty Business Services      USA    525.21M     503893.0   
4359    Security & Protection Services  Ireland     14.19B     503835.0   
3060                   Medical Devices      USA      1.53B     502153.0   
7009    Oil & Gas Refining & Marketing      USA     50.94B     500904.0   
4586             Recreational Vehicles      USA      3.70B     500656.0   

        market_cap  
2754  1.490000e+09  
2649  4.306360e+12  
212   2.294140e+12  
7153  9.450000e+09  
8547  4.158000e+10  
...            ...  
6706  5.252100e+08  
4359  1.419000e+10  
3060  1.530000e+09  
7009  5.094000e+10  
4586  3.700000e+09  

[1347 rows x 8 columns]

In [11]:
print(tickers['Country'].unique())

allowed_countries = [
    'USA', 'Canada', 'United Kingdom', 'Switzerland', 'Germany', 'France',
    'Netherlands', 'Japan', 'Australia', 'Denmark', 'Sweden', 'Norway',
    'Finland', 'Ireland', 'Belgium', 'Spain', 'Israel', 'Brazil', 'India'
]

# Filter tickers to include only allowed countries
tickers = tickers[tickers['Country'].isin(allowed_countries)]

print(tickers['Country'].unique())

tickers

['USA' 'China' 'Brazil' 'Canada' 'Denmark' 'Cayman Islands' 'Switzerland'
 'United Kingdom' 'Singapore' 'Australia' 'Finland' 'Netherlands' 'Taiwan'
 'Israel' 'India' 'Mexico' 'Sweden' 'South Africa' 'Belgium' 'Bermuda'
 'Spain' 'Ireland' 'Japan' 'Luxembourg' 'Germany' 'Hong Kong' 'Norway'
 'Colombia' 'Monaco' 'France' 'Italy' 'Turkey' 'Cyprus' 'Argentina']
['USA' 'Brazil' 'Canada' 'Denmark' 'Switzerland' 'United Kingdom'
 'Australia' 'Finland' 'Netherlands' 'Israel' 'India' 'Sweden' 'Belgium'
 'Spain' 'Ireland' 'Japan' 'Germany' 'Norway' 'France']


Ticker                    Company             Sector  \
2754   OPEN  Opendoor Technologies Inc        Real Estate   
2649   NVDA                NVIDIA Corp         Technology   
212    AMZN             Amazon.com Inc  Consumer Cyclical   
8547   VALE              Vale S.A. ADR    Basic Materials   
3486   SOFI      SoFi Technologies Inc          Financial   
...     ...                        ...                ...   
6706   KODK           Eastman Kodak Co        Industrials   
4359   ALLE               Allegion plc        Industrials   
3060   QDEL    QuidelOrtho Corporation         Healthcare   
7009    MPC    Marathon Petroleum Corp             Energy   
4586     BC             Brunswick Corp  Consumer Cyclical   

                              Industry  Country Market Cap       Volume  \
2754              Real Estate Services      USA      1.49B  126981253.0   
2649                    Semiconductors      USA   4306.36B  106136868.0   
212                    Internet Retail      USA   2294.14B   57251389.0   
8547  Other Industrial Metals & Mining   Brazil     41.58B   55509604.0   
3486                   Credit Services      USA     24.12B   53230046.0   
...                                ...      ...        ...          ...   
6706       Specialty Business Services      USA    525.21M     503893.0   
4359    Security & Protection Services  Ireland     14.19B     503835.0   
3060                   Medical Devices      USA      1.53B     502153.0   
7009    Oil & Gas Refining & Marketing      USA     50.94B     500904.0   
4586             Recreational Vehicles      USA      3.70B     500656.0   

        market_cap  
2754  1.490000e+09  
2649  4.306360e+12  
212   2.294140e+12  
8547  4.158000e+10  
3486  2.412000e+10  
...            ...  
6706  5.252100e+08  
4359  1.419000e+10  
3060  1.530000e+09  
7009  5.094000e+10  
4586  3.700000e+09  

[1269 rows x 8 columns]

#### **5. Download - Adjusted Close Prices**

In [12]:
if adjusted_closes_flag:
    # Define start and end dates
    end_date = datetime.today()
    start_date = datetime(end_date.year - 11, 10, 31)

    # Get the list of tickers
    tickers_list = tickers['Ticker'].unique().tolist()

    # Download adjusted close prices
    data = yf.download(
        tickers=tickers_list,
        start=start_date.strftime('%Y-%m-%d'),
        end=end_date.strftime('%Y-%m-%d'),
        progress=True,
        group_by='ticker',
        auto_adjust=False
    )

    # Extract only the adjusted close prices
    adjusted_closes = {
        ticker: data[ticker]['Adj Close']
        for ticker in tickers_list if ticker in data
    }

    # Combine into a single DataFrame
    df = pd.DataFrame(adjusted_closes)

    # Save to CSV (optional)
    df.to_csv(adjusted_close_prices_csv)

# Read the CSV file containing adjusted close prices
# index_col=0 => Use the first column (dates) as the DataFrame index
# parse_dates=True => Parse the index column as datetime objects
df = pd.read_csv(adjusted_close_prices_csv, index_col=0, parse_dates=True)

df

OPEN        NVDA        AMZN      VALE       SOFI        TSLA  \
Date                                                                        
2014-10-31   NaN    0.466931   15.273000  5.329594        NaN   16.113333   
2014-11-03   NaN    0.474817   15.286000  5.186979        NaN   16.172667   
2014-11-04   NaN    0.481030   15.140500  5.039082        NaN   15.928667   
2014-11-05   NaN    0.481030   14.826000  5.049646        NaN   15.398000   
2014-11-06   NaN    0.483180   14.832000  4.827801        NaN   16.081333   
...          ...         ...         ...       ...        ...         ...   
2025-07-28  2.34  176.750000  232.789993  9.840000  21.020000  325.589996   
2025-07-29  2.05  175.509995  231.009995  9.890000  22.400000  321.200012   
2025-07-30  2.07  179.270004  230.190002  9.630000  21.870001  319.040009   
2025-07-31  1.84  177.869995  234.110001  9.530000  22.580000  308.269989   
2025-08-01  2.10  173.720001  214.750000  9.710000  21.230000  302.630005   

            LCID  BBAI       INTC          F  ...       EXLS         WSM  \
Date                                          ...                          
2014-10-31   NaN   NaN  25.923483   8.019918  ...   5.598000   25.175978   
2014-11-03   NaN   NaN  26.152164   7.962998  ...   5.682000   25.148884   
2014-11-04   NaN   NaN  26.327475   7.940230  ...   5.794000   24.904984   
2014-11-05   NaN   NaN  25.901663   7.934539  ...   5.774000   25.059843   
2014-11-06   NaN   NaN  25.947691   8.076838  ...   5.786000   25.524416   
...          ...   ...        ...        ...  ...        ...         ...   
2025-07-28  2.79  7.15  20.680000  11.280000  ...  42.220001  188.229996   
2025-07-29  2.56  6.62  20.410000  11.080000  ...  42.200001  187.110001   
2025-07-30  2.50  6.41  20.340000  10.870000  ...  42.790001  190.529999   
2025-07-31  2.46  6.35  19.799999  11.070000  ...  43.430000  187.050003   
2025-08-01  2.42  6.40  19.309999  10.820000  ...  42.160000  187.669998   

                 CELC       EXG  LFST       KODK        ALLE       QDEL  \
Date                                                                      
2014-10-31        NaN  3.543701   NaN  21.570000   47.039684  28.549999   
2014-11-03        NaN  3.565114   NaN  21.670000   47.340923  28.209999   
2014-11-04        NaN  3.529426   NaN  20.870001   47.066261  27.719999   
2014-11-05        NaN  3.561545   NaN  23.480000   47.004250  28.290001   
2014-11-06        NaN  3.543701   NaN  22.900000   47.332066  28.680000   
...               ...       ...   ...        ...         ...        ...   
2025-07-28  36.790001  8.840000  4.17   6.930000  163.669998  26.090000   
2025-07-29  38.500000  8.810000  4.13   6.920000  164.110001  25.440001   
2025-07-30  40.299999  8.800000  4.23   6.860000  164.820007  24.290001   
2025-07-31  39.165001  8.750000  3.98   6.700000  165.919998  23.020000   
2025-08-01  39.910000  8.550000  3.79   6.450000  165.130005  22.809999   

                   MPC         BC  
Date                               
2014-10-31   32.622379  39.420841  
2014-11-03   32.880772  39.648262  
2014-11-04   32.525494  39.631420  
2014-11-05   32.554176  40.254749  
2014-11-06   33.422676  40.499020  
...                ...        ...  
2025-07-28  174.800003  60.310001  
2025-07-29  175.429993  61.189999  
2025-07-30  170.779999  59.160000  
2025-07-31  170.190002  58.290001  
2025-08-01  165.529999  56.639999  

[2703 rows x 1269 columns]

In [13]:
# Count the number of columns with at least one null value
null_counts = df.isnull().any(axis=0).sum()
print(f"{null_counts} columns contain at least one null value.")

# List columns that contain any null values
cols_with_nulls = df.columns[df.isnull().any()].tolist()
print("Columns with null values:", cols_with_nulls)

# Remove columns that contain any null values
df = df.loc[:, ~df.isnull().any()].copy()
df

425 columns contain at least one null value.
Columns with null values: ['OPEN', 'SOFI', 'LCID', 'BBAI', 'RKT', 'HOOD', 'AVTR', 'PLTR', 'JOBY', 'RIOT', 'APLD', 'QBTS', 'RGTI', 'SNAP', 'RIVN', 'RDDT', 'QS', 'HIMS', 'ACHR', 'SMR', 'SOUN', 'COIN', 'NVTS', 'ENVX', 'TLRY', 'IREN', 'OKLO', 'BITF', 'OSCR', 'FUBO', 'IONQ', 'RXRX', 'BE', 'HLN', 'RKLB', 'DOW', 'MP', 'CIFR', 'BTBT', 'AUR', 'MRNA', 'CLSK', 'CFLT', 'ROKU', 'CRCL', 'KHC', 'ADT', 'UBER', 'EOSE', 'PTON', 'RBLX', 'IR', 'CCCS', 'MIR', 'UWMC', 'NBIS', 'LYFT', 'CORZ', 'PYPL', 'COMP', 'SLDP', 'CRWV', 'PATH', 'OWL', 'HPE', 'USAR', 'PR', 'VRT', 'NFE', 'WSC', 'PINS', 'TMC', 'U', 'BULL', 'FSM', 'ZETA', 'SNOW', 'SHOP', 'GLXY', 'REPL', 'ASTS', 'KVUE', 'TOST', 'TTD', 'AMPX', 'TDOC', 'NET', 'XYZ', 'CPNG', 'TEM', 'RUN', 'LAC', 'VICI', 'AI', 'ARM', 'DJT', 'RBRK', 'ONON', 'ATAI', 'LUNR', 'RZLV', 'UPST', 'NVT', 'SG', 'ARRY', 'PL', 'ALAB', 'VST', 'PK', 'TNGX', 'NVST', 'MS', 'PCOR', 'IBRX', 'APP', 'DKNG', 'MBLY', 'DELL', 'S', 'GENI', 'MVST', 'FRSH', 'GDY

NVDA        AMZN      VALE        TSLA       INTC  \
Date                                                                  
2014-10-31    0.466931   15.273000  5.329594   16.113333  25.923483   
2014-11-03    0.474817   15.286000  5.186979   16.172667  26.152164   
2014-11-04    0.481030   15.140500  5.039082   15.928667  26.327475   
2014-11-05    0.481030   14.826000  5.049646   15.398000  25.901663   
2014-11-06    0.483180   14.832000  4.827801   16.081333  25.947691   
...                ...         ...       ...         ...        ...   
2025-07-28  176.750000  232.789993  9.840000  325.589996  20.680000   
2025-07-29  175.509995  231.009995  9.890000  321.200012  20.410000   
2025-07-30  179.270004  230.190002  9.630000  319.040009  20.340000   
2025-07-31  177.869995  234.110001  9.530000  308.269989  19.799999   
2025-08-01  173.720001  214.750000  9.710000  302.630005  19.309999   

                    F        AAPL         AMD  PLUG       LUMN  ...  \
Date                                                            ...   
2014-10-31   8.019918   23.889521    2.800000  4.71  20.505371  ...   
2014-11-03   7.962998   24.199198    2.870000  5.14  20.668507  ...   
2014-11-04   7.940230   24.022238    2.830000  5.35  20.579521  ...   
2014-11-05   7.934539   24.079760    2.800000  4.96  20.589418  ...   
2014-11-06   8.076838   24.148623    2.760000  5.12  19.279404  ...   
...               ...         ...         ...   ...        ...  ...   
2025-07-28  11.280000  214.050003  173.660004  1.77   4.470000  ...   
2025-07-29  11.080000  211.270004  177.440002  1.59   4.590000  ...   
2025-07-30  10.870000  209.050003  179.509995  1.55   4.460000  ...   
2025-07-31  11.070000  207.570007  176.309998  1.50   4.450000  ...   
2025-08-01  10.820000  202.380005  171.699997  1.40   3.710000  ...   

                  GRMN        ASB       EXLS         WSM       EXG       KODK  \
Date                                                                            
2014-10-31   40.026833  13.219654   5.598000   25.175978  3.543701  21.570000   
2014-11-03   40.185570  13.212624   5.682000   25.148884  3.565114  21.670000   
2014-11-04   40.286579  13.170435   5.794000   24.904984  3.529426  20.870001   
2014-11-05   40.113419  13.233721   5.774000   25.059843  3.561545  23.480000   
2014-11-06   39.637249  13.353255   5.786000   25.524416  3.543701  22.900000   
...                ...        ...        ...         ...       ...        ...   
2025-07-28  236.360001  25.410000  42.220001  188.229996  8.840000   6.930000   
2025-07-29  239.300003  25.230000  42.200001  187.110001  8.810000   6.920000   
2025-07-30  221.490005  25.170000  42.790001  190.529999  8.800000   6.860000   
2025-07-31  218.759995  24.740000  43.430000  187.050003  8.750000   6.700000   
2025-08-01  218.729996  24.090000  42.160000  187.669998  8.550000   6.450000   

                  ALLE       QDEL         MPC         BC  
Date                                                      
2014-10-31   47.039684  28.549999   32.622379  39.420841  
2014-11-03   47.340923  28.209999   32.880772  39.648262  
2014-11-04   47.066261  27.719999   32.525494  39.631420  
2014-11-05   47.004250  28.290001   32.554176  40.254749  
2014-11-06   47.332066  28.680000   33.422676  40.499020  
...                ...        ...         ...        ...  
2025-07-28  163.669998  26.090000  174.800003  60.310001  
2025-07-29  164.110001  25.440001  175.429993  61.189999  
2025-07-30  164.820007  24.290001  170.779999  59.160000  
2025-07-31  165.919998  23.020000  170.190002  58.290001  
2025-08-01  165.130005  22.809999  165.529999  56.639999  

[2703 rows x 844 columns]

#### **6. Calculate Monthly Log Returns**
- Portfolio models (Markowitz, Equal Weight, etc.) work on returns, not raw prices.
- Using monthly log returns avoids lookahead bias and is standard for multi-asset backtesting.
- Log returns are more robust, easier to analyze statistically, and preferred for multi-period backtests and portfolio analysis.

In [14]:
# Resample prices to monthly frequency (use last available price of each month)
monthly_prices = df.resample('ME').last()

# Calculate log returns: log(P_t / P_{t-1})
log_returns = np.log(monthly_prices / monthly_prices.shift(1)).dropna()

# Show the first rows
log_returns


NVDA      AMZN      VALE      TSLA      INTC         F  \
Date                                                                     
2014-11-30  0.074852  0.103119 -0.113210  0.011600  0.097533  0.110104   
2014-12-31 -0.044864 -0.087237 -0.096643 -0.094775 -0.026110 -0.014730   
2015-01-31 -0.043319  0.133092 -0.151505 -0.088365 -0.093823 -0.042160   
2015-02-28  0.142699  0.069799  0.053992 -0.001278  0.013483  0.105089   
2015-03-31 -0.052583 -0.021430 -0.272523 -0.074350 -0.061395 -0.012316   
...              ...       ...       ...       ...       ...       ...   
2025-04-30  0.004970 -0.031176 -0.069494  0.085029 -0.122085 -0.001996   
2025-05-31  0.215624  0.105843 -0.019523  0.205293 -0.027745  0.050782   
2025-06-30  0.156364  0.067792  0.061591 -0.086786  0.136086  0.044284   
2025-07-31  0.118521  0.064940 -0.018712 -0.030006 -0.123379  0.020074   
2025-08-31 -0.023608 -0.086317  0.018712 -0.018465 -0.025059 -0.022842   

                AAPL       AMD      PLUG      LUMN  ...      GRMN       ASB  \
Date                                                ...                       
2014-11-30  0.100731 -0.003578 -0.209438 -0.004045  ...  0.032279 -0.011902   
2014-12-31 -0.074606 -0.043963 -0.241638 -0.029623  ... -0.072446  0.008084   
2015-01-31  0.059612 -0.038173 -0.116534 -0.062822  ... -0.008936 -0.102800   
2015-02-28  0.096016  0.190717  0.142851  0.018393  ... -0.053547  0.108707   
2015-03-31 -0.031874 -0.148806 -0.173272 -0.077053  ... -0.033705 -0.002148   
...              ...       ...       ...       ...  ...       ...       ...   
2025-04-30 -0.044321 -0.053889 -0.439367 -0.101965  ... -0.150083 -0.021082   
2025-05-31 -0.055073  0.128782  0.011429  0.101965  ...  0.082645  0.049092   
2025-06-30  0.021281  0.248028  0.526610  0.110957  ...  0.032416  0.061291   
2025-07-31  0.011630  0.217121  0.006689  0.015855  ...  0.046982  0.014248   
2025-08-31 -0.025322 -0.026495 -0.068993 -0.181872  ... -0.000137 -0.026625   

                EXLS       WSM       EXG      KODK      ALLE      QDEL  \
Date                                                                     
2014-11-30  0.001428  0.136755  0.020146 -0.059206  0.014214 -0.024465   
2014-12-31  0.023970  0.014910 -0.049160  0.065675  0.030937  0.037341   
2015-01-31  0.023069  0.037620 -0.022390 -0.186846 -0.026493 -0.205832   
2015-02-28  0.172173  0.027727  0.069591  0.046116  0.066608  0.087011   
2015-03-31  0.063822 -0.009241  0.000104  0.006869  0.059594  0.049383   
...              ...       ...       ...       ...       ...       ...   
2025-04-30  0.026546 -0.018421  0.001088 -0.004758  0.064845 -0.229814   
2025-05-31 -0.052727  0.046114  0.068956 -0.102010  0.024833  0.098609   
2025-06-30 -0.049019  0.009904  0.026088 -0.005296  0.013586 -0.062215   
2025-07-31 -0.008255  0.139244  0.007520  0.170452  0.140859 -0.224706   
2025-08-31 -0.029679  0.003309 -0.023122 -0.038027 -0.004773 -0.009164   

                 MPC        BC  
Date                            
2014-11-30 -0.003524  0.062329  
2014-12-31  0.001885  0.031308  
2015-01-31  0.025487  0.057245  
2015-02-28  0.130723  0.001545  
2015-03-31 -0.025171 -0.052808  
...              ...       ...  
2025-04-30 -0.058512 -0.156475  
2025-05-31  0.162469  0.102733  
2025-06-30  0.032862  0.087341  
2025-07-31  0.024265  0.053743  
2025-08-31 -0.027763 -0.028715  

[130 rows x 844 columns]